In [7]:
import pandas as pd
import numpy as np
import math
from os.path import join
from collections import defaultdict
from matplotlib import pyplot as plt
from matplotlib import colors
from matplotlib.ticker import MaxNLocator
%matplotlib inline
plt.rcParams['font.family'] = 'IPAPGothic'

In [8]:
def gen_4graph(df, filename, avg=False):
    if avg:
        time_bench = df['time_avg'].values
    else:
        time_bench = df['time'].values
    bench_bench = df['bench'].values
    macro_bench = df['macro'].values
    ppn_bench = [int(x) for x in df['ppn'].values]
    omp_bench = [int(x) for x in df['omp_num_threads'].values]
    y = defaultdict()
    y["MPI process"] = defaultdict()
    y["OpenMP thread"] = defaultdict()
    y["SIMD"] = defaultdict()
    y["SIMD and RoA"] = defaultdict()
    y["SIMD"]['Default'] = []
    y["SIMD"]['SIMD'] = []
    y["SIMD and RoA"]['Default'] = []
    y["SIMD and RoA"]['SIMD'] = []
    y["SIMD and RoA"]['Restructure of Array'] = []
    for i in range(len(time_bench)):
        # ppn
        if ppn_bench[i] not in y["MPI process"]:
            y["MPI process"][ppn_bench[i]] = [time_bench[i]]
        else:
            y["MPI process"][ppn_bench[i]].append(time_bench[i])
        # omp
        if omp_bench[i] not in y["OpenMP thread"]:
            y["OpenMP thread"][omp_bench[i]] = [time_bench[i]]
        else:
            y["OpenMP thread"][omp_bench[i]].append(time_bench[i])

        if bench_bench[i]:
            y["SIMD"]["Default"].append(time_bench[i])
            y["SIMD and RoA"]["Default"].append(time_bench[i])
        elif macro_bench[i]:
            y["SIMD"]["SIMD"].append(time_bench[i])
            y["SIMD and RoA"]["Restructure of Array"].append(time_bench[i])
        else:
            y["SIMD"]["SIMD"].append(time_bench[i])
            y["SIMD and RoA"]["SIMD"].append(time_bench[i])

    fig, axes = plt.subplots(nrows=2, ncols=2, figsize=(20, 20), dpi=900)
    cmap = ['b', 'g', 'r', 'c', 'm', 'y', 'k']
    marker = ['o', 'x', '^', '*']
    row = 0
    col = 0
    for key in y:
        cnt1 = 0
        cnt2 = 0
    #     fig = plt.figure()
    #     ax = plt.subplot(111)
        for k in y[key]:
            x = [i for i in range(len(y[key][k]))]
    #         ax.scatter(x[:], y[key][k][:], c=cmap[cnt1], marker=marker[cnt2], label=k)
            axes[row, col].scatter(x[:], y[key][k][:], c=cmap[cnt1], marker=marker[cnt2], label=k)
            if cnt1 == len(cmap) - 1:
                cnt1 = 0
                cnt2 += 1
            else:
                cnt1 += 1
        axes[row, col].set_title(key, fontsize=20)
    #     axes[row, col].set_title(key)
        box = axes[row, col].get_position()
        axes[row, col].set_position([box.x0, box.y0, box.width * 0.8, box.height])
        axes[row, col].set_xlabel("順序", fontsize=18)
        axes[row, col].set_ylabel("実行時間(sec)", fontsize=18)
        axes[row, col].tick_params(axis='both', which='major', labelsize=15)
        axes[row, col].tick_params(axis='both', which='minor', labelsize=15)
        axes[row, col].xaxis.set_major_locator(MaxNLocator(integer=True))
        axes[row, col].yaxis.set_major_locator(MaxNLocator(integer=True))
        # Put a legend to the right of the current axis
        axes[row, col].legend(loc='center left', bbox_to_anchor=(1, 0.5), fontsize=15)
        if col == 1:
            row += 1
            col = 0
        else:
            col += 1
    plt.title(key)
    fig.savefig(join("/Users/hashmup/Dropbox/研究室/卒業論文/thesis/images", filename))
    plt.show()

In [9]:
df_bench_b = pd.read_csv("k/data/2018-01-29_10-26/result_all.csv")
df_bench_a = pd.read_csv("k/data/2018-01-29_17-12/result_all.csv")
df_bench_c = pd.read_csv("k/data/sub/result_all.csv")
df_bench_d = pd.read_csv("k/data/sub2/result_all.csv")
df_bench = pd.concat([df_bench_b, df_bench_a, df_bench_c, df_bench_d]).sort_values(by="time").reset_index(drop=True)
gen_4graph(df_bench, "k-bench.pdf")

In [10]:
df_bench_b = pd.read_csv("k/data/2018-01-29_10-26/result_all.csv")
df_bench_a = pd.read_csv("k/data/2018-01-29_17-12/result_all.csv")
df_bench_c = pd.read_csv("k/data/sub/result_all.csv")
df_bench_d = pd.read_csv("k/data/sub2/result_all.csv")
df_bench = pd.concat([df_bench_b, df_bench_a, df_bench_c, df_bench_d]).sort_values(by="time").reset_index(drop=True)
df_bench = df_bench[:int(len(df_bench)/ 4.0)]
df_bench
# df_bench_avg.to_csv("t.csv")
gen_4graph(df_bench, "k-bench-top25.pdf")

In [11]:
# df_bench_b_avg = pd.read_csv("k/data/2018-01-29_10-26/result_candidate.csv")
# df_bench_a_avg = pd.read_csv("k/data/2018-01-29_17-12/result_candidate.csv")
# df_bench_avg = pd.concat([df_bench_b_avg, df_bench_a_avg]).sort_values(by=["time", "ppn"]).reset_index(drop=True)
# df_bench_avg['time_avg'] = (df_bench_avg['time'] + df_bench_avg['time0'] + df_bench_avg['time1']) / 3.0
# df_bench_avg = df_bench_avg.sort_values(by="time_avg").reset_index(drop=True)
# df_bench_avg = df_bench_avg[df_bench_avg["ppn"] >= 6.0]

# gen_4graph(df_bench_avg, "k-bench-adjusted1.pdf", True)

In [12]:
df_bench_b = pd.read_csv("k/data/2018-01-29_10-26/result_all.csv")
df_bench_a = pd.read_csv("k/data/2018-01-29_17-12/result_all.csv")
df_bench_c = pd.read_csv("k/data/sub/result_all.csv")
df_bench_d = pd.read_csv("k/data/sub2/result_all.csv")
df_bench = pd.concat([df_bench_b, df_bench_a, df_bench_c, df_bench_d]).sort_values(by="time").reset_index(drop=True)
df_bench = df_bench[:int(len(df_bench)/ 4.0)]
df_bench_avg = df_bench[(df_bench["ppn"] >=8.0)
                           ]
gen_4graph(df_bench_avg, "k-bench-adjusted-final.pdf")